# Extração da característica relação sinal-ruído (SNR) de dados de EEG

A relação sinal-ruído (SNR, do inglês _Signal-to-Noise Ratio_) é uma medida que compara o nível do sinal desejado com o nível do ruído de fundo. Uma SNR mais alta indica um sinal mais forte em comparação ao ruído, enquanto uma SNR mais baixa indica que o ruído é comparativamente forte.

O objetivo é utilizar um conjunto de dados com nível de atividade cerebral basal (que será considerado e utilizado como "ruído") e "removê-lo" do sinal obtido no experimento a fim de reconhecer os padrões de foco com maior clareza.

No contexto da caracterização de foco, podemos, a partir do sinal basal, classificar os sinais dos ritmos cerebrais com a presença ou não de foco, de forma que as amostras de sinais extraídas de um buffer sejam rotuladas com com a presença ou não de foco.

Esta análise será realizada com o auxílio do classificador SVM (_Support Vector Machine_). Nesse sentido, uma porcetagem das amostras são utilizadas para treino e outra para o teste (70 e 30% respectivamente).

In [246]:
import mne
import copy
import numpy as np
from scipy.signal import welch
import matplotlib.pyplot as plt

from sklearn.svm import SVC
from sklearn.feature_selection import RFE
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report


In [247]:
# Transform a string that represents a time value ("min:sec") into number and converts it to seconds
def convert_min_to_sec(time):
    minutes, seconds = map(int, time.split(":"))
    return minutes * 60 + seconds

# Transfor a string thats represents a range time "0:21 - 0:40" into index that will be used to cut data
def convert_time_range_to_index(timerange):
    start, end = map(str, timerange.split(" - "))
    new_start = convert_min_to_sec(start)
    new_end = convert_min_to_sec(end)
    
    index = []
    index.append(new_start * 250)
    index.append(new_end * 250)

    return index

In [248]:
n_channels = 8
ch_types = ['eeg'] * n_channels
sfreq = 250
ch_names = ["F3", "Fz", "F4", "C3", "Cz", "C4", "P3", "P4"]
info = mne.create_info(ch_names=ch_names, sfreq=sfreq, ch_types=ch_types)
info.set_montage("standard_1020")

<Info | 8 non-empty values
 bads: []
 ch_names: F3, Fz, F4, C3, Cz, C4, P3, P4
 chs: 8 EEG
 custom_ref_applied: False
 dig: 11 items (3 Cardinal, 8 EEG)
 highpass: 0.0 Hz
 lowpass: 125.0 Hz
 meas_date: unspecified
 nchan: 8
 projs: []
 sfreq: 250.0 Hz
>

In [249]:
ia = '../dataset-s7/IA/OpenBCI-RAW-2023-09-28_16-51-25_IA.txt'
ia_ob = np.loadtxt(ia, delimiter=',', skiprows=5, usecols=range(1, 9))

basal = '../dataset-s7/TF/OpenBCI-RAW-2023-11-07_13-17-01_TF.txt'
basal_ob = np.loadtxt(basal, delimiter=',', skiprows=5, usecols=range(1, 9))

In [250]:
# Aula IA
ia_timeranges = [
    "6:00 - 10:17",
]

# Basal (TF)
basal_timerange = [
    "3:28 - 4:28"
]

In [251]:
ia_index = []
ia_index = convert_time_range_to_index(ia_timeranges[0])

basal_index = []
basal_index = convert_time_range_to_index(basal_timerange[0])

data_cut_ia = ia_ob[ia_index[0]:ia_index[1], :]
data_cut_basal = basal_ob[basal_index[0]:basal_index[1], :]

print(data_cut_ia.shape)

X = {
    'ia': mne.io.RawArray(data_cut_ia.T, info),
    'basal': mne.io.RawArray(data_cut_basal.T, info),
}

(64250, 8)
Creating RawArray with float64 data, n_channels=8, n_times=64250
    Range : 0 ... 64249 =      0.000 ...   256.996 secs
Ready.
Creating RawArray with float64 data, n_channels=8, n_times=15000
    Range : 0 ... 14999 =      0.000 ...    59.996 secs
Ready.


### Filtragem dos dados

O laço a seguir aplica dois filtros nos dados. Primeiramente, atenua-se com um filtro _notch_ a frequência de 60Hz de forma a evitar a interferência da rede elétrica e, posteriormente, obtém-se a faixa de frequência desejada de 4 a 100Hz com um filtro passa faixa.

In [252]:
# TODO: filtrar corretamente os dados que são usados para SNR (basal)

for key in X:
    X[key].notch_filter(freqs=60)
    X[key].filter(l_freq=4, h_freq=100)

# X['ia'].notch_filter(freqs=60)
# X['ia'].filter(l_freq=4, h_freq=100)

Filtering raw data in 1 contiguous segment
Setting up band-stop filter from 59 - 61 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandstop filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 59.35
- Lower transition bandwidth: 0.50 Hz (-6 dB cutoff frequency: 59.10 Hz)
- Upper passband edge: 60.65 Hz
- Upper transition bandwidth: 0.50 Hz (-6 dB cutoff frequency: 60.90 Hz)
- Filter length: 1651 samples (6.604 s)

Filtering raw data in 1 contiguous segment
Setting up band-pass filter from 4 - 1e+02 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 4.00
- Lower transition bandwidth: 2.00 Hz (-6 dB cutoff frequency: 3.00 Hz)
- Upper passband e

Método auxiliar responsável pela rotulação de uma amostra. Dada uma amostra (psd), retorna os rótulos 'focus' ou 'not_focus'. A função determina o rótulo através do cálculo de qual banda de frequência é a dominante ao longo de uma janela de tempo específica.

In [253]:
def label_data(freqs, psd):
    
    # Definindo os limites das bandas de frequência (em Hz)
    theta_band = (4, 8)       # Theta: 4 - 8 Hz
    alpha_band = (8, 13)      # Alpha: 8 - 13 Hz
    beta_band = (13, 30)      # Beta: 13 - 30 Hz
    gamma_band = (30, 100)    # Gamma: 30 - 100 Hz
    
    # Calculando a média dos 8 eletrodos (transformando em um ndarray unidimensional)
    X_avg = np.average(psd, axis=0)

    # Encontrando os índices correspondentes às frequências de interesse
    theta_idxs = np.where((freqs >= theta_band[0]) & (freqs <= theta_band[1]))[0]
    alpha_idxs = np.where((freqs >= alpha_band[0]) & (freqs <= alpha_band[1]))[0]
    beta_idxs = np.where((freqs >= beta_band[0]) & (freqs <= beta_band[1]))[0]
    gamma_idxs = np.where((freqs >= gamma_band[0]) & (freqs <= gamma_band[1]))[0]

    # Calculando a potência em cada banda de frequência por meio da integração da PSD
    bands = [
        np.sum(X_avg[theta_idxs]),
        np.sum(X_avg[alpha_idxs]),
        np.sum(X_avg[beta_idxs]),
        np.sum(X_avg[gamma_idxs])
    ]
    
    # Determinando qual banda é a dominante (maior potência)
    dominant_band = np.argmax(bands)
    
    # Identificando se a banda dominante nesse trecho é beta ou gamma
    if dominant_band == 2 or dominant_band == 3:
        return 'focus' # se sim, rotula esse trecho como "focus"
    else:
        return 'not_focus' # se não, rotula como "not_focus"

    

### Janela Deslizante

In [254]:
sr = 250            # Taxa de amostragem dos dados do EEG (250Hz)
jump = 5            # Tamanho da janela de análise (5 em 5 segundos)
size = sr * jump    # Número de pontos de dados em cada janela de análise

samples = {
    'X': [], # Amostras
    'Y': []  # Rótulos
}

# Obtendo apenas os dados da aula IA
data = X['ia'].copy()
data.set_eeg_reference(ref_channels='average', projection=False)

# Percorre os dados em incrementos de sr (1 segundo) extraindo janelas de tamanho size (5s)
for i in range(0, int(data.times[-1] - jump), 1):
    
    # Calculando o intervalo da janela em termos de tempo (tmin = i, tmax = i + 5seg)
    tmin = i
    tmax = i + jump

    # Obtendo os dados da janela/intervalo calculada
    cut = data.copy().crop(tmin=tmin, tmax=tmax).get_data()
    

    # Número de pontos por segmento
    n_per_seg = 128

    # Quantidade de sobreposição entre segmentos
    n_overlap = n_per_seg // 2 # 64
    
    # Calculando a densidade espectral de potência (PSD)
    freqs, cut_psd = welch(cut, fs=sr, nperseg=n_per_seg, noverlap=n_overlap)
    print(cut_psd.shape)
    
    # Rotulando a amostra de 5 seg (cut_psd) como "focus" ou "not_focus"
    label = label_data(freqs, cut_psd)
    print(cut_psd.T.shape)
    # Associando uma amostra a um rótulo no dict samples
    # (cada posição i da lista X (amostra) é respectiva ao rótulo da posição i do array Y)
    samples['X'].append(cut_psd.T)
    samples['Y'].append(label)

print(len(samples['X']))
print(len(samples['X'][0]))
print(len(samples['X'][0][0]))

EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(65, 8)
(8, 65)
(

### Estimando o ruído de fundo através do sinal basal

In [255]:
# Convertendo o tipo dos dados filtrados de objeto RawArray para ndarray
ndarray_data_basal = X['basal'].copy().get_data()

# Transformando os dados de basal para o domínio da frequência
_, data_basal_frequency = welch(ndarray_data_basal, fs=250, nperseg=512, noverlap=256)

# Normalizando os dados com Standard Scaler
scaler = StandardScaler()
basal_normalized = scaler.fit_transform(data_basal_frequency.T)

# Lista que armazena as médias de potência para cada canal
noise_power = []

for channel_data in basal_normalized:
    # fft_result = np.fft.fft(channel_data)

    # # densidade espectral de potência (PSD)
    # psd = np.abs(fft_result) ** 2
    
    # média da potência no intervalo de tempo sem estímulo
    base_power = np.mean(channel_data)
    noise_power.append(base_power)

# média das médias de potência de todos os canais para estimar o ruído de fundo
estimated_background_noise = np.mean(noise_power)
print(estimated_background_noise)

5.529515453385994e-17


### Relação Sinal-Ruído de Banda Estreita

Banda estreita refere-se a sinais em que a largura de banda do sinal é pequena em relação à frequência central do sinal. Nesse sentido, a SNR de banda estreita é aplicada quando o sinal e o ruído ocupam uma faixa de frequência muito restrita. Ela pode ser observada pela seguinte equação:

$SNR_{banda\ estreita} = 10 \cdot \log_{10}\left(\frac{\text{energia total do espectro}}{\text{média das amplitudes nas frequências vizinhas}}\right)$

### Relação Sinal-Ruído de Banda Larga

Por outro lado, banda larga refere-se a sinais onde a largura de banda do sinal é grande, abrangendo uma ampla faixa de frequências. Dessa maneira, a SNR de banda larga aplica-se a situações nas quais tanto o sinal quanto o ruído ocupam uma larga faixa de frequências é definido da seguinte forma:

$SNR_{banda\ larga} = 10 \cdot \log_{10}\left(\frac{\text{energia total do espectro}}{\text{energia total do espectro de amplitude}}\right)$

### Aplicando as SNRs de Banda Estreita e Larga para o sinal de interesse

In [256]:
# Criando cópias profundas das listas para garantir que as originais não sejam modificadas
X_copy = copy.deepcopy(samples['X']) # 251 elementos
Y_copy = copy.deepcopy(samples['Y']) # 251 elementos

# Lista de ndarrays (aqui, cada ndarray é uma amostra de 5 seg de dados)
array_of_ndarrays = X_copy
narrow_band_SNR_list = []
wide_band_SNR_list = []

# Calculando as características SNRs sobre cada amostra
for ndarray in array_of_ndarrays:

    sample_normalized = scaler.fit_transform(ndarray)

    # Subtração matricial entre cada elemento de uma lista de amostra e o ruído de fundo (sinal basal)
    target_amplitudes_adjusted = sample_normalized - estimated_background_noise

    # Obtendo a SNR de banda estreita
    narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
    print(narrow_band_SNR)
    narrow_band_SNR_list.append(narrow_band_SNR)
    print(narrow_band_SNR.shape)

    # Obtendo a SNR de banda larga
    total_power = np.sum(target_amplitudes_adjusted)
    wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
    print(wide_band_SNR)
    wide_band_SNR_list.append(wide_band_SNR)
    print(wide_band_SNR.shape)

[[         nan          nan          nan          nan          nan
           nan          nan          nan]
 [164.84212744 162.09603478 160.55948194 161.94907265 164.39966996
  166.59383163 158.53723625 165.2620226 ]
 [170.02857834 169.17925995 168.6330959  168.66963013 168.77520118
  170.3820645  168.40806773 169.89848217]
 [169.12627334 169.43690276 169.46036365 166.88209123 168.08898589
  167.95956383 167.67695338 169.24559944]
 [165.91963172 167.21385219 167.71674062 162.87958829 167.25339359
  161.90386073 163.08958924 165.98686937]
 [162.58897008 165.08824452 166.00973397 165.73253352 168.31685995
  164.71255884 158.70818032 162.29766833]
 [158.08472256 162.51315154 162.34202113 164.88975843 165.30778691
  161.75988797 160.84707531 160.34036818]
 [155.42885229 156.49052574 160.3278088  158.70757181 157.52892565
  157.17975307          nan 156.3141887 ]
 [156.01021821 156.63925948 159.20486926 150.39495619 149.56825963
  156.48894429 144.66620413          nan]
 [152.78543922 158.

[[         nan          nan          nan          nan          nan
           nan          nan 137.00656317]
 [162.478617   161.8200244  162.69125066 159.75871152 164.34715255
  161.7481624  159.14235712 166.34999561]
 [169.49512852 168.36805329 168.14648393 166.65616122 169.08972198
  169.30555136 167.36585183 170.15523857]
 [169.31859792 169.84549693 168.94444471 165.84995479 167.61882881
  168.53778995 167.97158023 168.80273238]
 [166.53104254 167.49017595 167.7882592  163.43045225 167.0431441
  166.54481512 166.93994907 164.709964  ]
 [164.21217108 163.16809305 165.51048178 167.09996388 168.30014603
  166.92497556 165.88560067 159.66253375]
 [163.09179607 163.84922106 165.93681058 168.85371221 165.85445746
  165.80374435 166.38906482 162.21135193]
 [161.24698428 161.61131003 164.92499032 163.3961788  154.48730714
  161.94291781 160.79128296 159.11206622]
 [161.65791853 161.20600787 160.74644716 155.20764411          nan
  158.10853244          nan 145.14112041]
 [159.92750265 160.7

/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplit

[[         nan          nan          nan          nan 154.07997048
  133.08422711          nan          nan]
 [162.155773   164.95854335 162.50861054 163.03327615 167.06276759
  166.52581713 159.79242204 163.9322301 ]
 [169.51763462 169.82672756 169.07916574 169.11544093 170.54399899
  170.56464694 168.11541588 169.61821242]
 [168.80164541 168.99366086 169.97851334 168.44324337 168.1775844
  167.49074417 168.73073149 169.22376   ]
 [164.9655172  165.89839904 165.61555822 166.22360913 162.46492896
  164.56854682 166.02648115 167.22517449]
 [166.61524771 163.71922776 163.29273398 164.33781974 157.39590504
  162.62976182 161.42822136 163.68535364]
 [165.63146882 163.62366377 162.34894104 160.00212075 147.29355824
  159.2425453  161.83433914 160.59026386]
 [163.66226122 161.69589221 163.34294415          nan          nan
  156.83422276 161.77499479 158.32532575]
 [159.94737559 158.58840466 158.43673059 156.63789738          nan
  151.32809419 160.51472552 157.04606466]
 [155.90511241 154.6

/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplit

...

/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplit

[[         nan          nan          nan          nan 152.03773355
           nan          nan          nan]
 [159.08862954 161.25448643 164.59041144          nan 166.00402229
           nan          nan 166.6525405 ]
 [168.94408777 168.37650445 169.13732828 163.78727515 169.54107499
  161.14261704 166.61210881 170.7171889 ]
 [167.15621275 166.07546723 167.72636494 164.74409812 168.72835397
           nan 164.82191199 167.12121915]
 [166.04161974 165.84564813 168.08578178 164.39671926 166.21827235
           nan 165.73978214 163.63080412]
 [168.99488602 169.73491999 165.18357553 167.80414892 166.16439748
           nan 161.77677519 162.99479289]
 [166.302171   165.72821952 160.65326848 163.00954406 163.99911338
           nan 155.7928597  157.54775594]
 [159.07483612 157.54738153 160.09391102          nan 155.9719612
           nan          nan          nan]
 [         nan 151.16762114 158.69253605 158.89384529 143.8473866
           nan          nan          nan]
 [         nan 146.27

/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplit

[[131.71382336 134.20144732 133.38455116 135.54720412          nan
  133.01415182 137.66755399          nan]
 [         nan          nan          nan          nan          nan
           nan          nan          nan]
 [         nan          nan          nan          nan          nan
           nan          nan          nan]
 [         nan          nan          nan          nan          nan
           nan          nan          nan]
 [         nan          nan          nan          nan          nan
           nan          nan          nan]
 [         nan          nan          nan          nan          nan
           nan          nan          nan]
 [         nan          nan          nan          nan          nan
           nan 133.46989698 126.85036707]
 [         nan          nan          nan 125.81615431          nan
           nan 132.52032948 121.15366189]
 [         nan          nan          nan          nan          nan
           nan 133.41565298 122.994329  ]
 [         nan     

/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplitudes_adjusted / total_power)
/tmp/ipykernel_3956/3542301611.py:19: RuntimeWarning: invalid value encountered in log10
  narrow_band_SNR = 10 * np.log10(target_amplitudes_adjusted / estimated_background_noise)
/tmp/ipykernel_3956/3542301611.py:26: RuntimeWarning: invalid value encountered in log10
  wide_band_SNR = 10 * np.log10(target_amplit

In [257]:
# teste (TODO: apagar)
print(len(wide_band_SNR_list))
print(len(wide_band_SNR))

print(len(narrow_band_SNR_list))
print(len(narrow_band_SNR))

251
65
251
65


In [261]:
snrw_nparray = np.array(wide_band_SNR_list)

snrn_nparray = np.array(narrow_band_SNR_list)

print(snrw_nparray.shape)
print(snrn_nparray.shape)



snrw_transposed = snrw_nparray.transpose(0, 2, 1)
snrn_transposed = snrn_nparray.transpose(0, 2, 1)

# Calculando a média ao longo do eixo 65
snrw_mean = snrw_transposed.mean(axis=2)
snrn_mean = snrn_transposed.mean(axis=2)


print(snrw_mean.shape)
print(snrn_mean.shape)

snr_feature = np.concatenate((snrw_mean, snrn_mean), axis=1)
print(snr_feature.shape)


(251, 65, 8)
(251, 65, 8)
(251, 8)
(251, 8)
(251, 16)


### Classificador SVM

In [263]:
X = np.array(snr_feature)  # features (atributos de entrada)
y = np.array(Y_copy)  # labels (rótulos de saída)

# Dividindo os dados em treino (70%) e teste (30%)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

# Instanciando o classificador SVM
svm_model = SVC(kernel='linear')

# Treinando o modelo SVM com as características selecionadas
svm_model.fit(X_train, y_train)

# Realizando a predição nos dados de teste
y_pred = svm_model.predict(X_test)

# Avaliando o desempenho (acurácia)
accuracy = accuracy_score(y_test, y_pred)
print(f"Acurácia do SVM: {accuracy * 100:.2f}%")


# Aplicando a redução de dimensionalidade RFE para obter apenas 10 características
# selector = RFE(svm_model, n_features_to_select=10, step=1)
# selector = selector.fit(X_train, y_train)

ValueError: Input X contains NaN.
SVC does not accept missing values encoded as NaN natively. For supervised learning, you might want to consider sklearn.ensemble.HistGradientBoostingClassifier and Regressor which accept missing values encoded as NaNs natively. Alternatively, it is possible to preprocess the data, for instance by using an imputer transformer in a pipeline or drop samples with missing values. See https://scikit-learn.org/stable/modules/impute.html You can find a list of all estimators that handle NaN values at the following page: https://scikit-learn.org/stable/modules/impute.html#estimators-that-handle-nan-values

### Tarefa para aplicação das características SNR:

Agora que temos os dois vetores de características SNR, podemos utilizar buffers com e sem a evocação dos rítmos que caracterizam o foco.

#### Divisão dos dados

Utilizando a iteração (por exemplo, de 5 segundos caracterizada pela janela) realizada no sinal a cada ~1 segundo, realize a rotulação dos dados de interesse (Beta e Gamma). Ou seja, cada amostra será um sinal de 5 segundos (1250 pontos de 8 canais). A janela que não for qualificada como Beta ou Gama por exemplo, poderá ser rotulada com "desfoque". Se acharem interessante, adicionar rótulos do ritmo Theta também.

No caso do sinal que representa o basal (se tiverem) poderá pegar um único sinal de aproximadamente 30 segundos para ser utilizado na equação de ruído, que irá ter como resultado um único valor. Lembrando que o valor de ruído deve atuar no sinal no domínio da frequência.

#### Classificação

Cálculo: diferença entre tempo inicial (em minutos) e final (tbm em min) dada por: (tempo_min * 60) * 250. Aplicando aos dados reais para criar o vetor de características:

- Diferença: 90000 - 154250 com 8 canais
- Pontos totais: 64250 com 8 canais

- 64.250 (pontos totais) / 250 (taxa de amostragem) = 257 segundos
- 257 / 5 (tamanho da janela sem sobreposição) = 51 amostras (51,4)

<br>

Em nossos dados simulados, temos 150.000 pontos com 8 canais. A utilização desses dados funcionará da seguinte forma para a criação do vetor de características:

- 150.000 (pontos totais) / 250 (taxa de amostragem) = 600 segundos
- 600 / 5 (tamanho da janela sem sobreposição) = 120 amostras

|     | SNRw1                | SNRw2 | ... | SNRw8 | SNRn1 | SNRn2 | ... | SNRn8 |
|-----|----------------------|-------|-----|-------|-------|-------|-----|-------|
| 1   | [w1, w2, ..., w65]   |       |     |       |       |       |     |       |
| 2   |                      |       |     |       |       |       |     |       |
| ... |                      |       |     |       |       |       |     |       |
| 251 |                      |       |     |       |       |       |     |       |

- Agora transforme cada um dos vetores de pontos no domínio da frequência (65 pontos) em um único valor real. Neste caso pode ser utilizado tanto a média como a mediana (ou ambos). Se utilizarmos as duas, teremos no final 32 colunas de características:
    - 8 canais
    - SNR narrow e SNR wide (2)
    - Média e mediana (2)

|     | 1   | ... | 32 |
|-----|-----|-----|----|
| 1   | w'  | ... |    |
| 2   | ... |     |    |
| ... |     |     |    |
| 120 |     |     |    |



Após obter o vetor de característica, realizar a divisão dos dados em treinamento e teste (normalmente uma proporção de 70 e 30% respectivamente) e aplicar para o classificador SVM.

**PLUS**: Ao final da tarefa, verificar a melhora dos resultados utilizando um seletor de características. Neste caso, podemos utilizar o RFE (*Recursive Feature Elimination*) em uma fase anterior a classificação para reduzir as 32 características se for necessário.


